In [17]:
import numpy as np
import matplotlib.pyplot as plt
import librosa
from IPython.display import Audio, display
from scipy import signal

# audio example
samples, fs = librosa.load("audio_examples/voice.wav", sr=44100)

# **Time-varying Filters**

## **Wah-wah**
The wah-wah effect is implemented by modulating the center frequency of a bandpass filter. This implementation uses an IIR allpass-based bandpass filter with a time-varying center frequency.

### **Center Frequency Modulation**
The center frequency varies sinusoidally according to:

$\large f_c(t) = f_{c\_center} + \Delta f \cdot \sin(2\pi \cdot f_m \cdot M \cdot t)$

where:
- $f_{c\_center}$ : Center frequency of the filter (typically 2kHz)
- $\Delta f$ : Frequency deviation (sweep range)
- $f_m$ : Base modulation frequency
- $M$ : Frequency multiplier (determines modulation speed)
- $t$ : Time

### **Effect Variations**
The multiplier M creates different sonic characteristics:
- **Wah-wah** (M=1): Classic periodic sweep
- **M-fold wah** (M=5-20): Tremolo-like effect
- **Bell** (M=100): Ring modulator/bell-like sound

In [39]:
def coeffs(fc, fb, fs):
    tan = np.tan(np.pi * fb / fs)
    return (tan - 1) / (tan + 1), -np.cos(2 * np.pi * fc / fs)

## Allpass based bandpass with a wah wah/
def wah_wah_filter(x, fs, fm, q_factor, delta_f, fc_center=2000, M=1):
    N = len(x)
    t = np.arange(N) / fs
    
    fc_t = fc_center + delta_f * np.sin(2 * np.pi * fm * M * t)
    
    y = np.zeros(N)
    x_h = np.zeros(N)
    
    for n in range(N):
        fb = fc_t[n] / q_factor
        
        c, d = coeffs(fc_t[n], fb, fs)
        
        # Apply filter
        if n == 0:
            x_h[n] = x[n]
            y[n] = -c * x_h[n]
        elif n == 1:
            x_h[n] = x[n] - d * (1 - c) * x_h[n - 1]
            y[n] = -c * x_h[n] + d * (1 - c) * x_h[n - 1]
        else:
            x_h[n] = x[n] - d * (1 - c) * x_h[n - 1] + c * x_h[n - 2]
            y[n] = -c * x_h[n] + d * (1 - c) * x_h[n - 1] + x_h[n - 2]
    
    return 0.5 * (x - y)

def auto_wah(samples, fs, preset="wah-wah"):
    presets = {
        "wah-wah": {
            "M": 1,
            "Q_factor": 8, 
            "delta_f": 1000,
            "fm": 2.0 
        },
        "m-fold": {
            "M": 10,  
            "Q_factor": 4,  #
            "delta_f": 800,  
            "fm": 2.0
        },
        "bell": {
            "M": 100,
            "Q_factor": 8,
            "delta_f": 1000,
            "fm": 2.0
        }
    }
    
    params = presets[preset]
    return wah_wah_filter(
        samples, 
        fs,
        params["fm"],
        params["Q_factor"],
        params["delta_f"],
        fc_center=2000,
        M=params["M"]
    )
    
wah = auto_wah(samples, fs, preset="wah-wah")
mfold = auto_wah(samples, fs, preset='m-fold')
bell = auto_wah(samples, fs, preset='bell')

print("Wah-wah")
display(Audio(wah, rate=fs))
print("m-fold")
display(Audio(mfold, rate=fs))
print("Bell")
display(Audio(bell, rate=fs))


Wah-wah


m-fold


Bell


## **Phaser**

<img src="diagrams/phaser.png" width="70%">


A phaser effect is created by cascading multiple second-order IIR allpass sections. The allpass filters produce frequency-dependent phase shifts, creating notches in the frequency response when combined with the original signal. An LFO modulates the notch frequencies, causing the characteristic sweeping effect.

The implementation consists of two key components:
1. A cascade of allpass filters providing time-varying phase shifts
2. A feedforward/feedback configuration that creates constructive and destructive interference at different frequencies

When the phase-shifted signal combines with the original signal, frequencies where the phase difference is 180° are canceled, while those at 360° are reinforced. As the LFO modulates the filter parameters, these notches sweep across the frequency spectrum, producing the classic phaser sound.

In [102]:
def coeffs(fc, fb, fs):
    tan = np.tan(np.pi * fb / fs)
    return (tan - 1) / (tan + 1), -np.cos(2 * np.pi * fc / fs)

class Allpass:
    def __init__(self):
        self.x_h_1 = 0.0  # x_h[n-1]
        self.x_h_2 = 0.0  # x_h[n-2]

    def process(self, x_n, c, d):
        x_h_n = x_n
        x_h_n -= d * (1 - c) * self.x_h_1
        x_h_n += c * self.x_h_2

        y_n = -c * x_h_n
        y_n += d * (1 - c) * self.x_h_1
        y_n += self.x_h_2

        # internal states
        self.x_h_2 = self.x_h_1
        self.x_h_1 = x_h_n

        return y_n

def phaser(x, fs, lfo_freq=0.8, depth=1.0, n_ap=3, mix=1.0, feedback=0.3, fc_minmax=[500, 1200]):
    N = len(x)
    y = np.zeros(N)
    v = np.zeros(N)
    
    depth = np.clip(depth, 0.0, 1.0)
    mix = np.clip(mix, 0.0, 1.0)
    bandwidth = 0.9  #  ratio of fc
    fc_min = fc_minmax[0]
    fc_max = fc_minmax[1]

    allpasses = [Allpass() for _ in range(n_ap)]
    
    for n in range(N):
        LFO = np.sin(2 * np.pi * lfo_freq * n / fs)
        fc = fc_min + depth * (fc_max - fc_min) * (LFO + 1) / 2
        
        fb = fc * bandwidth
        c, d = coeffs(fc, fb, fs)
        ap_out = x[n] + feedback * v[n - 1] if n > 0 else x[n]
        
        for ap_filter in allpasses:
            ap_out = ap_filter.process(ap_out, c, d)
        v[n] = ap_out
        
        y[n] = x[n] + mix * v[n]
    
    y = y / np.max(np.abs(y))
    
    return y
    
y = phaser(samples, fs)
display(Audio(y, rate=fs))